## Introduction

Imagine standing at the check-out counter at the grocery store with a long line behind you and the cashier not-so-quietly announces that your card has been declined. In this moment, you probably aren’t thinking about the data science that determined your fate.<br><br>
Embarrassed, and certain you have the funds to cover everything needed for an epic nacho party for 50 of your closest friends, you try your card again. Same result. As you step aside and allow the cashier to tend to the next customer, you receive a text message from your bank. “Press 1 if you really tried to spend $500 on cheddar cheese.”<br><br>
While perhaps cumbersome (and often embarrassing) in the moment, this fraud prevention system is actually saving consumers millions of dollars per year. Researchers from the IEEE Computational Intelligence Society (IEEE-CIS) want to improve this figure, while also improving the customer experience. With higher accuracy fraud detection, you can get on with your chips without the hassle.<br><br>
The data comes from Vesta's real-world e-commerce transactions and contains a wide range of features from device type to product features. You also have the opportunity to create new features to improve your results.<br><br>
More details on this Kaggle competition can be found [here](https://www.kaggle.com/c/ieee-fraud-detection/overview).

### Data Description

We are predicting the probability that an online transaction is fraudulent, as denoted by the binary target `isFraud`. The data is broken into two files `identity` and `transaction`, which are joined by `TransactionID`. Not all transactions have corresponding identity information.<br><br>
**Transaction Table**<br>
- TransactionDT: timedelta from a given reference datetime (not an actual timestamp)
- TransactionAMT: transaction payment amount in USD
- ProductCD: product code, the product for each transaction
- card1 - card6: payment card information, such as card type, card category, issue bank, country, etc.
- addr: address
- dist: distances between (not limited) billing address, mailing address, zip code, IP address, phone area, etc.
- P_ and (R__) emaildomain: purchaser and recipient email domain
- C1-C14: counting, such as how many addresses are found to be associated with the payment card, etc. The actual meaning is masked.
- D1-D15: timedelta, such as days between previous transaction, etc.
- M1-M9: match, such as names on card and address, etc.
- Vxxx: Vesta engineered rich features, including ranking, counting, and other entity relations.<br>

Categorical Features in this table
- `ProductCD`
- `card1` - `card6`
- `addr1` , `addr2`
- `P_emaildomain`
- `R_emaildomain`
- `M1` - `M9`<br><br>

**Identity Table**<br>
Variables in this table are identity information – network connection information (IP, ISP, Proxy, etc) and digital signature (UA/browser/os/version, etc) associated with transactions. They're collected by Vesta’s fraud protection system and digital security partners. (The field names are masked and pairwise dictionary will not be provided for privacy protection and contract agreement)<br>

Categorical Features in this table
- `DeviceType`
- `DeviceInfo`
- `id_12` - `id_38`<br><br>

**Files**
- train_{transaction, identity}.csv - the training set
- test_{transaction, identity}.csv - the test set (you must predict the `isFraud` value for these observations)
- sample_submission.csv - a sample submission file in the correct format





## Exploratory Data Analysis

Let us unzip the `ieee-fraud-detection.zip` file present in the `input` folder and move it to `data` folder.

In [1]:
#Unzipping the files,
!unzip 'input/ieee-fraud-detection.zip' -d 'data/'

Archive:  input/ieee-fraud-detection.zip
  inflating: data/test_identity.csv  
  inflating: data/test_transaction.csv  
  inflating: data/train_identity.csv  
  inflating: data/sample_submission.csv  
  inflating: data/train_transaction.csv  


In [2]:
#Printing the contents in the data directory
import os
print(os.listdir("data/"))

['sample_submission.csv', 'test_identity.csv', 'test_transaction.csv', 'train_identity.csv', 'train_transaction.csv']


In [3]:
#Importing the essentials

# Disable warnings in Anaconda
import warnings
warnings.filterwarnings('ignore')

#Visualization libraries
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()

#For more info on arguments of seaborn.set()
#https://seaborn.pydata.org/generated/seaborn.set.html

#Graphics in SVG format are more sharp and legible
%config InlineBackend.figure_format = 'svg'

#Increase the default plot size and set the color scheme
plt.rcParams['figure.figsize'] = (8,5)
#This works as well - plt.rcParams['figure.figsize'] = 8,5
plt.rcParams['image.cmap'] = 'viridis'

import numpy as np
import pandas as pd
import time

### Loading and Reading the dataset

In [4]:
%%time

df_transact_train = pd.read_csv('data/train_transaction.csv')
df_id_train = pd.read_csv('data/train_identity.csv')
df_transact_test = pd.read_csv('data/test_transaction.csv')
df_id_test = pd.read_csv('data/test_identity.csv')
sample_submission = pd.read_csv('data/sample_submission.csv')

CPU times: user 45.3 s, sys: 40.8 s, total: 1min 26s
Wall time: 1min


In [5]:
#Printing the shapes of the dataframe(s)
print('Shape of df_transact_train dataframe{}'.format(df_transact_train.shape))
print('Shape of df_id_train dataframe{}'.format(df_id_train.shape))
print('Shape of df_transact_test dataframe{}'.format(df_transact_test.shape))
print('Shape of df_id_test dataframe{}'.format(df_id_test.shape))
print('Shape of sample_submission dataframe{}'.format(sample_submission.shape))

Shape of df_transact_train dataframe(590540, 394)
Shape of df_id_train dataframe(144233, 41)
Shape of df_transact_test dataframe(506691, 393)
Shape of df_id_test dataframe(141907, 41)
Shape of sample_submission dataframe(506691, 2)


### Merging dataset(s)

As per the problem statement, the data is broken into two files `identity` and `transaction`, which are joined by `TransactionID`. Not all transactions have corresponding identity information. Since _not all transactions have corresponding identity information_ we will use a (left) outer join, using pandas `merge` function as a key might not appear in both tables.

In [6]:
#Merging 'df_transact_train' and 'df_id_train'
df_train = pd.merge(df_transact_train, df_id_train, how = 'left', on = 'TransactionID')

#Merging 'df_transact_test' and 'df_id_test'
df_test = pd.merge(df_transact_test, df_id_test, how = 'left', on = 'TransactionID')

#Reducing the memory usage
del df_transact_train, df_id_train, df_transact_test, df_id_test

#Setting the index as 'TransactionID'
#df_train = df_train.set_index('TransactionID', drop = 'True')

In [7]:
#Print the shape of the new train and test dataframe(s)
print("Training dataset has {} rows and {} columns".format(df_train.shape[0], df_train.shape[1]))
print("Test dataset has {} rows and {} columns".format(df_test.shape[0], df_test.shape[1]))

Training dataset has 590540 rows and 434 columns
Test dataset has 506691 rows and 433 columns


In [8]:
#Displaying first 5 rows of df_train dataset
df_train.head()

TransactionID  isFraud  TransactionDT  TransactionAmt ProductCD  card1  \
0        2987000        0          86400            68.5         W  13926   
1        2987001        0          86401            29.0         W   2755   
2        2987002        0          86469            59.0         W   4663   
3        2987003        0          86499            50.0         W  18132   
4        2987004        0          86506            50.0         H   4497   

   card2  card3       card4  card5  ...                id_31  id_32  \
0    NaN  150.0    discover  142.0  ...                  NaN    NaN   
1  404.0  150.0  mastercard  102.0  ...                  NaN    NaN   
2  490.0  150.0        visa  166.0  ...                  NaN    NaN   
3  567.0  150.0  mastercard  117.0  ...                  NaN    NaN   
4  514.0  150.0  mastercard  102.0  ...  samsung browser 6.2   32.0   

       id_33           id_34  id_35 id_36 id_37  id_38  DeviceType  \
0        NaN             NaN    NaN   NaN   NaN    NaN         NaN   
1        NaN             NaN    NaN   NaN   NaN    NaN         NaN   
2        NaN             NaN    NaN   NaN   NaN    NaN         NaN   
3        NaN             NaN    NaN   NaN   NaN    NaN         NaN   
4  2220x1080  match_status:2      T     F     T      T      mobile   

                      DeviceInfo  
0                            NaN  
1                            NaN  
2                            NaN  
3                            NaN  
4  SAMSUNG SM-G892A Build/NRD90M  

[5 rows x 434 columns]

In [9]:
#Displaying first 5 rows of df_test dataset
df_test.head()

TransactionID  TransactionDT  TransactionAmt ProductCD  card1  card2  \
0        3663549       18403224           31.95         W  10409  111.0   
1        3663550       18403263           49.00         W   4272  111.0   
2        3663551       18403310          171.00         W   4476  574.0   
3        3663552       18403310          284.95         W  10989  360.0   
4        3663553       18403317           67.95         W  18018  452.0   

   card3       card4  card5  card6  ...  id_31  id_32  id_33  id_34 id_35  \
0  150.0        visa  226.0  debit  ...    NaN    NaN    NaN    NaN   NaN   
1  150.0        visa  226.0  debit  ...    NaN    NaN    NaN    NaN   NaN   
2  150.0        visa  226.0  debit  ...    NaN    NaN    NaN    NaN   NaN   
3  150.0        visa  166.0  debit  ...    NaN    NaN    NaN    NaN   NaN   
4  150.0  mastercard  117.0  debit  ...    NaN    NaN    NaN    NaN   NaN   

  id_36  id_37  id_38  DeviceType  DeviceInfo  
0   NaN    NaN    NaN         NaN         NaN  
1   NaN    NaN    NaN         NaN         NaN  
2   NaN    NaN    NaN         NaN         NaN  
3   NaN    NaN    NaN         NaN         NaN  
4   NaN    NaN    NaN         NaN         NaN  

[5 rows x 433 columns]

In [10]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 590540 entries, 0 to 590539
Columns: 434 entries, TransactionID to DeviceInfo
dtypes: float64(399), int64(4), object(31)
memory usage: 1.9+ GB


In [11]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 506691 entries, 0 to 506690
Columns: 433 entries, TransactionID to DeviceInfo
dtypes: float64(399), int64(3), object(31)
memory usage: 1.6+ GB


`df_train` has 434 columns(features), out of which 399 are `float`, 4 are `int64` and 31 are `object` datatypes.<br>
`df_test` has 433 columns(features), out of which 399 are `float`, 3 are `int64` and 31 are `object` datatypes.

Since there are so many features in both train and test dataset(s), `df.columns` will not list all the features. In order to list all the features, we need to take the help of indexing.

In [12]:
#Function to display all the columns
def list_of_entire_features(df):
    first_set_of_100_features = df.columns[0:100]
    second_set_of_100_features = df.columns[101:200]
    third_set_of_100_features = df.columns[201:300]
    fourth_set_of_100_features = df.columns[301:400]
    rem_features = df.columns[401:]
    return first_set_of_100_features, second_set_of_100_features, third_set_of_100_features, fourth_set_of_100_features, rem_features

In [13]:
#Printing the features of training dataset
list_of_entire_features(df_train)

(Index(['TransactionID', 'isFraud', 'TransactionDT', 'TransactionAmt',
        'ProductCD', 'card1', 'card2', 'card3', 'card4', 'card5', 'card6',
        'addr1', 'addr2', 'dist1', 'dist2', 'P_emaildomain', 'R_emaildomain',
        'C1', 'C2', 'C3', 'C4', 'C5', 'C6', 'C7', 'C8', 'C9', 'C10', 'C11',
        'C12', 'C13', 'C14', 'D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8',
        'D9', 'D10', 'D11', 'D12', 'D13', 'D14', 'D15', 'M1', 'M2', 'M3', 'M4',
        'M5', 'M6', 'M7', 'M8', 'M9', 'V1', 'V2', 'V3', 'V4', 'V5', 'V6', 'V7',
        'V8', 'V9', 'V10', 'V11', 'V12', 'V13', 'V14', 'V15', 'V16', 'V17',
        'V18', 'V19', 'V20', 'V21', 'V22', 'V23', 'V24', 'V25', 'V26', 'V27',
        'V28', 'V29', 'V30', 'V31', 'V32', 'V33', 'V34', 'V35', 'V36', 'V37',
        'V38', 'V39', 'V40', 'V41', 'V42', 'V43', 'V44', 'V45'],
       dtype='object'),
 Index(['V47', 'V48', 'V49', 'V50', 'V51', 'V52', 'V53', 'V54', 'V55', 'V56',
        'V57', 'V58', 'V59', 'V60', 'V61', 'V62', 'V63', 'V64', 

In [14]:
#Printing the features of test dataset
list_of_entire_features(df_test)

(Index(['TransactionID', 'TransactionDT', 'TransactionAmt', 'ProductCD',
        'card1', 'card2', 'card3', 'card4', 'card5', 'card6', 'addr1', 'addr2',
        'dist1', 'dist2', 'P_emaildomain', 'R_emaildomain', 'C1', 'C2', 'C3',
        'C4', 'C5', 'C6', 'C7', 'C8', 'C9', 'C10', 'C11', 'C12', 'C13', 'C14',
        'D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'D10', 'D11',
        'D12', 'D13', 'D14', 'D15', 'M1', 'M2', 'M3', 'M4', 'M5', 'M6', 'M7',
        'M8', 'M9', 'V1', 'V2', 'V3', 'V4', 'V5', 'V6', 'V7', 'V8', 'V9', 'V10',
        'V11', 'V12', 'V13', 'V14', 'V15', 'V16', 'V17', 'V18', 'V19', 'V20',
        'V21', 'V22', 'V23', 'V24', 'V25', 'V26', 'V27', 'V28', 'V29', 'V30',
        'V31', 'V32', 'V33', 'V34', 'V35', 'V36', 'V37', 'V38', 'V39', 'V40',
        'V41', 'V42', 'V43', 'V44', 'V45', 'V46'],
       dtype='object'),
 Index(['V48', 'V49', 'V50', 'V51', 'V52', 'V53', 'V54', 'V55', 'V56', 'V57',
        'V58', 'V59', 'V60', 'V61', 'V62', 'V63', 'V64', 'V65', 'V66

### Converting the data-type(s) of the features

As per the problem statement, following features are categorical,<br>

_Transaction_ table - `ProductCD`, `card1` - `card6`, `addr1` , `addr2`, `P_emaildomain`, `R_emaildomain`, `M1` - `M9`<br>
_Identity_ table - `DeviceType`, `DeviceInfo`, `id_12` - `id_38` <br>

Either we can verify if this holds true for each of the above feature(s) like below (for `card1` - `card6` features) or we can convert all these features to `object` datatype irrespective of the the datatype(s) they current belong to. This can be done using `astype()`

In [15]:
#Number of features having dtype = int64 in df_train
df_train.select_dtypes(include='int64').nunique()

TransactionID    590540
isFraud               2
TransactionDT    573349
card1             13553
dtype: int64

In [16]:
##Number of features having dtype = object in df_train
df_train.select_dtypes(include = np.object).nunique()

ProductCD           5
card4               4
card6               4
P_emaildomain      59
R_emaildomain      60
M1                  2
M2                  2
M3                  2
M4                  3
M5                  2
M6                  2
M7                  2
M8                  2
M9                  2
id_12               2
id_15               3
id_16               2
id_23               3
id_27               2
id_28               2
id_29               2
id_30              75
id_31             130
id_33             260
id_34               4
id_35               2
id_36               2
id_37               2
id_38               2
DeviceType          2
DeviceInfo       1786
dtype: int64

In [17]:
df_train[[x for x in df_train if 'card' in x]].info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 590540 entries, 0 to 590539
Data columns (total 6 columns):
card1    590540 non-null int64
card2    581607 non-null float64
card3    588975 non-null float64
card4    588963 non-null object
card5    586281 non-null float64
card6    588969 non-null object
dtypes: float64(3), int64(1), object(2)
memory usage: 31.5+ MB


In [18]:
#Function to convert features datatype
def convert_datatype(df):
    
    card_cols = [x for x in df.columns if 'card' in x]
    for col in card_cols:
        df[card_cols] = df[card_cols].astype('object')
    
    addr_cols = [x for x in df.columns if 'addr' in x]
    for col in addr_cols:
        df[addr_cols] = df[addr_cols].astype('object')
    
    M_cols = [x for x in df.columns if 'M' in x]
    for col in M_cols:
        df[M_cols] = df[M_cols].astype('object')
    
    id_cols = [x for x in df.columns if 'id' in x]
    for col in id_cols:
        df[id_cols] = df[id_cols].astype('object')
    
    df['P_emaildomain'] = df['P_emaildomain'].astype('object')
    df['R_emaildomain'] = df['R_emaildomain'].astype('object')
    df['DeviceType'] = df['DeviceType'].astype('object')
    df['DeviceInfo'] = df['DeviceInfo'].astype('object')
    
    return df

In [19]:
#Applying the above function to 'df_train' and 'df_test'

#Try to use tqdm here LATER!!!
df_train = convert_datatype(df_train)
df_test = convert_datatype(df_test)

In [20]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 590540 entries, 0 to 590539
Columns: 434 entries, TransactionID to DeviceInfo
dtypes: float64(371), int64(3), object(60)
memory usage: 1.9+ GB


In [21]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 506691 entries, 0 to 506690
Columns: 433 entries, TransactionID to DeviceInfo
dtypes: float64(371), int64(2), object(60)
memory usage: 1.6+ GB


We can observe that the count of features having `object` datatype has increased in both training and test dataset(s).

## Data Visualization

- We generally try to plot the following when we first see a dataset:

    - Correlation Matrix
    - Histogram of all features
    - tSNE (project your data in 3-D) (t-distributed Stochastic Neighbor Embedding)<br>
    
- Explore Single features one by one

    - numeric
    - categorical
    - binary(special feature of categorical)
    - not necessary to treat ordinal features different from categorical when it comes to visualisation<br>
    
- Feature Interaction

    - num-num(interaction b/w numeric feature-numeric feature) , Visualization - ScatterPlot
    - cat-cat , Visualization - CountPlot
    - num-cat , Visualization - BoxPlot<br>

In [22]:
#Since 'TransactionID' is just ID we will exclude that feature since there is no meaningful statistic to infer from it

#Setting the feature(s) list for `df_train` dataset
useful_columns_train = ['isFraud', 'TransactionDT', 'TransactionAmt', 'ProductCD']
card_columns_train = [x for x in df_train.columns if 'card' in x]
addr_columns_train = [x for x in df_train.columns if 'addr' in x]
dist_columns = ['dist1', 'dist2']
email_columns = ['P_emaildomain', 'R_emaildomain']
C_columns = ['C1', 'C2', 'C3', 'C4', 'C5', 'C6', 'C7', 'C8', 'C9', 'C10', 'C11', 'C12', 'C13', 'C14']
D_columns = ['D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'D10', 'D11', 'D12', 'D13', 'D14']
M_columns_train = [x for x in df_train.columns if 'M' in x]
V_columns_train = [x for x in df_train.columns if 'V' in x]
id_columns_train = [x for x in df_train.columns if 'id' in x]
device_columns = ['DeviceType', 'DeviceInfo']

#Setting the feature(s) list for `df_test` dataset
useful_columns_train = ['isFraud', 'TransactionDT', 'TransactionAmt', 'ProductCD']
card_columns_test = [x for x in df_test.columns if 'card' in x]
addr_columns_test = [x for x in df_test.columns if 'addr' in x]
dist_columns = ['dist1', 'dist2']
email_columns = ['P_emaildomain', 'R_emaildomain']
C_columns = ['C1', 'C2', 'C3', 'C4', 'C5', 'C6', 'C7', 'C8', 'C9', 'C10', 'C11', 'C12', 'C13', 'C14']
D_columns = ['D1', 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'D10', 'D11', 'D12', 'D13', 'D14']
M_columns_test = [x for x in df_test.columns if 'M' in x]
V_columns_test = [x for x in df_test.columns if 'V' in x]
id_columns_test = [x for x in df_test.columns if 'id' in x]
device_columns = ['DeviceType', 'DeviceInfo']

### Explore Features one by one

#### Numeric Features

In [23]:
##Number of features NOT having dtype = object in df_train
df_train.select_dtypes(exclude = np.object).nunique()

TransactionID     590540
isFraud                2
TransactionDT     573349
TransactionAmt     20902
dist1               2651
dist2               1751
C1                  1657
C2                  1216
C3                    27
C4                  1260
C5                   319
C6                  1328
C7                  1103
C8                  1253
C9                   205
C10                 1231
C11                 1476
C12                 1199
C13                 1597
C14                 1108
D1                   641
D2                   641
D3                   649
D4                   808
D5                   688
D6                   829
D7                   597
D8                 12353
D9                    24
D10                  818
                   ...  
V310               19136
V311                3098
V312                8068
V313                5529
V314               11377
V315                6973
V316                9814
V317               15184
V318               12309


Since nearly all predictors have been anonymized, I decided to focus on the non-anonymized predictors time and amount of the transaction during my EDA. The data set contains 284,807 transactions. The mean value of all transactions is $88.35 while the largest transaction recorded in this data set amounts to $25,691.16. However, as you might be guessing right now based on the mean and maximum, the distribution of the monetary value of all transactions is heavily right-skewed. The vast majority of transactions are relatively small and only a tiny fraction of transactions comes even close to the maximum.

We will calculate stats for `TransactionAmt` feature in `df_train` and `df_test`

In [24]:
#Displaying stat(s)
df_train['TransactionAmt'].describe()

count    590540.000000
mean        135.027176
std         239.162522
min           0.251000
25%          43.321000
50%          68.769000
75%         125.000000
max       31937.391000
Name: TransactionAmt, dtype: float64

In [25]:
#Displaying stat(s)
df_test['TransactionAmt'].describe()

count    506691.000000
mean        134.725568
std         245.779822
min           0.018000
25%          40.000000
50%          67.950000
75%         125.000000
max       10270.000000
Name: TransactionAmt, dtype: float64

In [27]:
sns.boxplot(x = 'TransactionAmt', data = df_train)

Mean value for `TransactionAmt` in `df_test` : 134.72

### Dealing with Missing Values

Since the dataset contains many features, to find any pattern it's essential to divide the dataframe into sub-dataframe(s) meaning creating new dataframe(s) consisting of related feature(s).<br>
We already have seen there are many `NaN` values, what we should do next is investigate if there are missing observations for some columns that are marked as a `zero value`. We can verify this by the definition of those columns and the domain knowledge that a zero value is invalid for those measures, e.g. a zero for email_columns(as initialized below) is invalid.<br>
In order to do the same, we can use `df.describe()` to print summary statistics on each attribute, focus on the `min` value for each of them and see for ourselves whether there can actually be a minimum value of `zero` for that attribute or if it is because of presence of null-values.<br>
But since, this dataset doesn't contain any `zero` values for null values, we will skip this step.

In [ ]:
print(f'There are {df_train.isnull().any().sum()} columns in training dataset with missing values.')
print(f'There are {df_test.isnull().any().sum()} columns in testing dataset with missing values.')

We will either have to drop the columns having missing values or impute them. <br>

**Strategy 1**
- Drop the columns/features having more than 50% missing values as it will not be convenient to impute these values since most of the attribute values will be guessed.
- 

**Strategy 2** 

- Impute all the NaN values 


In [ ]:
#Number of null values in each feature of 'df_train'
df_train.isnull().sum()[1:100]

In [ ]:
#Percentage of null values in each feature of 'df_train'
df_train.isnull().sum()/len(df_train)

In [ ]:
#Number of null values in each feature of 'df_test'
df_test.isnull().sum()

In [ ]:
#Percentage of null values in each feature of 'df_test'
df_test.isnull().sum()/len(df_test)

In [ ]:
def miss_values_gr_50(df):
    missing_values = df.isnull().sum()/len(df)
    cols_miss_values_50 = df.columns[missing_values > 0.5]
    df = df.drop(cols_miss_values_50, axis=1)
    return df
    

In [ ]:
df_train = miss_values_gr_50(df_train)
df_test = miss_values_gr_50(df_test)

In [ ]:
print(f'There are {df_train.isnull().any().sum()} columns in training dataset with missing values.')
print(f'There are {df_test.isnull().any().sum()} columns in testing dataset with missing values.')

In [ ]:
df_train.isnull().sum()